As respostas da **Questão 1** ("Qual a média de valor total (total\_amount) recebido em um mês
considerando todos os yellow táxis da frota?") estão na **célula 6** e as respostas da **questão 2** ("Qual a média de passageiros (passenger\_count) por cada hora do dia
que pegaram táxi no mês de maio considerando todos os táxis da
frota?") estão na **célula 32 (ultima célula)** . 

deixo todas as análises feitas para avaliarem a linha de raciocínio.

Obrigado por avaliarem!

In [0]:
%sql
select * from curated_nyc_taxi.yellow_taxi_curated
limit 5

VendorID passenger_count total_amount tpep_pickup_datetime tpep_dropoff_datetime taxi_color 2 1.0 11.1 2023-03-01T00:06:43.000Z 2023-03-01T00:16:43.000Z yellow_taxi 2 2.0 76.49 2023-03-01T00:08:25.000Z 2023-03-01T00:39:30.000Z yellow_taxi 1 0.0 28.05 2023-03-01T00:15:04.000Z 2023-03-01T00:29:26.000Z yellow_taxi 1 1.0 24.7 2023-03-01T00:49:37.000Z 2023-03-01T01:01:05.000Z yellow_taxi 2 1.0 14.64 2023-03-01T00:08:04.000Z 2023-03-01T00:11:06.000Z yellow_taxi

**Verificando se há nulos no total_amount do yellow taxi**

In [0]:
%sql
select
count(1)
from curated_nyc_taxi.yellow_taxi_curated
where total_amount is null

count(1) 0

Resolução Q1

In [0]:
%sql
-- questão 1
select
date_trunc('MONTH',tpep_pickup_datetime) as month,
ROUND(AVG(total_amount), 2) AS media_valor_total
from curated_nyc_taxi.yellow_taxi_curated
group by 1
order by 1

month media_valor_total 2023-01-01T00:00:00.000Z 27.02 2023-02-01T00:00:00.000Z 26.9 2023-03-01T00:00:00.000Z 27.8 2023-04-01T00:00:00.000Z 28.27 2023-05-01T00:00:00.000Z 28.96

**> Resposta q1: A média mensal pode variar entre 26.9 e 28.96 dolares**

**Resolução Q2:**

verificando valores nulos na tabela yellow taxi

In [0]:
%sql
select 
count(1)
from curated_nyc_taxi.yellow_taxi_curated
where tpep_pickup_datetime >= date '2023-05-01'
and tpep_pickup_datetime <  date '2023-06-01'
and passenger_count is null

count(1) 101796

**verificando valores não nulos na tabela yellow taxi**

In [0]:
%sql
select 
count(1)
from curated_nyc_taxi.yellow_taxi_curated
where tpep_pickup_datetime >= date '2023-05-01'
and tpep_pickup_datetime <  date '2023-06-01'
and passenger_count is not null

count(1) 3411849

**CONSIDERAÇÕES**

mesmo fazendo o coalesce na camada de preprocessamento com os valores da coluna _rescued_data , ainda temos 101.796 registros nulos no campo passenger_count contra 3.411.849 não nulos no df de yellow_taxi. o que representa 2,98% de valores nulos nessa coluna. Sabemos que dados de corridas de taxi são passíveis de sazonalidade, e para não perdê-la na análise, vale a pena imputar nos nulos a média do período



In [0]:
%sql
--descobrindo a média de passenger_count dos yellow_taxis sem valor nulo, APENAS NO PERÍODO SOLICITADO
select 
round(avg(passenger_count),2) as media_passageiros_yellow
from curated_nyc_taxi.yellow_taxi_curated
where tpep_pickup_datetime >= date '2023-05-01'
and tpep_pickup_datetime <  date '2023-06-01'
and passenger_count is not null

media_passageiros_yellow 1.36

In [0]:
%sql
select *,
coalesce(passenger_count, 1.36) as passenger_count_imputed 
from curated_nyc_taxi.yellow_taxi_curated
where tpep_pickup_datetime >= timestamp '2023-05-01'
and tpep_pickup_datetime < timestamp '2023-06-01'

VendorID passenger_count total_amount tpep_pickup_datetime tpep_dropoff_datetime taxi_color passenger_count_imputed 1 0.0 51.65 2023-05-01T00:33:13.000Z 2023-05-01T00:53:01.000Z yellow_taxi 0.0 1 2.0 57.15 2023-05-01T00:42:49.000Z 2023-05-01T01:11:18.000Z yellow_taxi 2.0 1 2.0 64.2 2023-05-01T00:56:34.000Z 2023-05-01T01:13:39.000Z yellow_taxi 2.0 2 1.0 47.09 2023-05-01T00:00:52.000Z 2023-05-01T00:20:12.000Z yellow_taxi 1.0 1 0.0 59.15 2023-05-01T00:05:50.000Z 2023-05-01T00:19:41.000Z yellow_taxi 0.0 1 0.0 69.0 2023-05-01T00:42:54.000Z 2023-05-01T01:04:49.000Z yellow_taxi 0.0 2 1.0 64.56 2023-05-01T00:50:34.000Z 2023-05-01T01:12:09.000Z yellow_taxi 1.0 1 1.0 14.35 2023-05-01T00:13:58.000Z 2023-05-01T00:18:10.000Z yellow_taxi 1.0 2 1.0 19.9 2023-05-01T00:28:47.000Z 2023-05-01T00:39:33.000Z yellow_taxi 1.0 2 1.0 78.67 2023-05-01T00:18:49.000Z 2023-05-01T00:43:41.000Z yellow_taxi 1.0 1 1.0 53.5 2023-05-01T00:52:48.000Z 2023-05-01T01:17:35.000Z yellow_taxi 1.0 2 1.0 14.64 2023-05-01T00:55:22.000Z 2023-05-01T00:58:20.000Z yellow_taxi 1.0 2 1.0 19.1 2023-05-01T00:28:12.000Z 2023-05-01T00:36:09.000Z yellow_taxi 1.0 2 2.0 76.89 2023-05-01T00:04:27.000Z 2023-05-01T00:26:38.000Z yellow_taxi 2.0 1 1.0 9.4 2023-05-01T00:07:05.000Z 2023-05-01T00:08:45.000Z yellow_taxi 1.0 1 1.0 17.25 2023-05-01T00:30:56.000Z 2023-05-01T00:36:33.000Z yellow_taxi 1.0 2 1.0 83.88 2023-05-01T00:47:34.000Z 2023-05-01T01:17:55.000Z yellow_taxi 1.0 2 1.0 10.8 2023-05-01T00:53:26.000Z 2023-05-01T00:57:47.000Z yellow_taxi 1.0 2 1.0 69.55 2023-05-01T00:34:15.000Z 2023-05-01T00:51:43.000Z yellow_taxi 1.0 1 1.0 5.5 2023-05-01T00:14:01.000Z 2023-05-01T00:14:23.000Z yellow_taxi 1.0 1 1.0 85.75 2023-05-01T00:15:57.000Z 2023-05-01T00:46:34.000Z yellow_taxi 1.0 2 1.0 98.76 2023-05-01T00:44:34.000Z 2023-05-01T01:25:25.000Z yellow_taxi 1.0 1 1.0 55.5 2023-05-01T00:13:31.000Z 2023-05-01T00:29:06.000Z yellow_taxi 1.0 1 1.0 18.0 2023-05-01T00:34:39.000Z 2023-05-01T00:45:59.000Z yellow_taxi 1.0 2 1.0 27.0 2023-05-01T00:07:58.000Z 2023-05-01T00:21:31.000Z yellow_taxi 1.0 1 2.0 72.7 2023-05-01T00:45:50.000Z 2023-05-01T01:17:48.000Z yellow_taxi 2.0 1 1.0 85.15 2023-05-01T00:19:37.000Z 2023-05-01T00:49:42.000Z yellow_taxi 1.0 2 1.0 64.05 2023-05-01T00:46:14.000Z 2023-05-01T01:09:19.000Z yellow_taxi 1.0 2 1.0 82.3 2023-05-01T00:24:27.000Z 2023-05-01T00:48:51.000Z yellow_taxi 1.0 2 1.0 15.7 2023-05-01T00:02:13.000Z 2023-05-01T00:09:26.000Z yellow_taxi 1.0 2 2.0 11.5 2023-05-01T00:10:47.000Z 2023-05-01T00:15:01.000Z yellow_taxi 2.0 2 3.0 -10.88 2023-05-01T00:30:22.000Z 2023-05-01T00:36:54.000Z yellow_taxi 3.0 2 3.0 13.6 2023-05-01T00:30:22.000Z 2023-05-01T00:36:54.000Z yellow_taxi 3.0 2 1.0 61.74 2023-05-01T00:13:37.000Z 2023-05-01T00:36:14.000Z yellow_taxi 1.0 2 1.0 85.56 2023-05-01T00:33:02.000Z 2023-05-01T01:01:04.000Z yellow_taxi 1.0 2 1.0 14.9 2023-05-01T00:11:17.000Z 2023-05-01T00:15:46.000Z yellow_taxi 1.0 2 2.0 92.3 2023-05-01T00:16:06.000Z 2023-05-01T00:49:43.000Z yellow_taxi 2.0 2 1.0 16.44 2023-05-01T00:50:02.000Z 2023-05-01T00:55:05.000Z yellow_taxi 1.0 2 1.0 61.65 2023-05-01T00:50:14.000Z 2023-05-01T01:13:03.000Z yellow_taxi 1.0 2 1.0 49.3 2023-05-01T00:51:46.000Z 2023-05-01T01:05:46.000Z yellow_taxi 1.0 2 1.0 14.64 2023-05-01T00:17:46.000Z 2023-05-01T00:22:08.000Z yellow_taxi 1.0 2 1.0 68.89 2023-05-01T00:06:30.000Z 2023-05-01T00:28:28.000Z yellow_taxi 1.0 2 1.0 90.3 2023-05-01T00:55:23.000Z 2023-05-01T01:25:40.000Z yellow_taxi 1.0 2 1.0 72.06 2023-05-01T00:46:55.000Z 2023-05-01T01:06:09.000Z yellow_taxi 1.0 2 1.0 95.1 2023-05-01T00:45:52.000Z 2023-05-01T01:13:11.000Z yellow_taxi 1.0 1 1.0 72.6 2023-05-01T00:13:55.000Z 2023-05-01T00:36:55.000Z yellow_taxi 1.0 1 1.0 14.3 2023-05-01T00:52:39.000Z 2023-05-01T00:59:19.000Z yellow_taxi 1.0 2 1.0 21.36 2023-05-01T00:00:48.000Z 2023-05-01T00:09:57.000Z yellow_taxi 1.0 1 1.0 54.15 2023-05-01T00:22:14.000Z 2023-05-01T00:55:35.000Z yellow_taxi 1.0 1 1.0 96.65 2023-05-01T00:38:46.000Z 2023-05-01T01:14:23.000Z yellow_taxi 1.0 2 1.0 54

**criando tabela temporária yellow taxi com o coalesce da média nos passenger_count null**

In [0]:
df_y_med_pas_count = spark.sql(
  "select *, "
  "coalesce(passenger_count, 1.36) as passenger_count_imputed "
  "from curated_nyc_taxi.yellow_taxi_curated "
  "where tpep_pickup_datetime >= timestamp '2023-05-01' "
  "and tpep_pickup_datetime < timestamp '2023-06-01'"
)
df_y_med_pas_count.createOrReplaceTempView("df_y_med_pas_count")

**Agora fazendo o mesmo processo para o green taxi**

In [0]:
%sql
select 
count(1)
from curated_nyc_taxi.green_taxi_curated
where lpep_pickup_datetime >= date '2023-05-01'
and lpep_pickup_datetime <  date '2023-06-01'
and passenger_count is null

count(1) 4732

In [0]:
%sql
select 
count(1)
from curated_nyc_taxi.green_taxi_curated
where lpep_pickup_datetime >= date '2023-05-01'
and lpep_pickup_datetime <  date '2023-06-01'
and passenger_count is not null

count(1) 64436

**CONSIDERAÇÕES**

mesmo fazendo o coalesce na camada de preprocessamento com os valores da coluna _rescued_data , ainda temos 4732 registros nulos no campo passenger_count contra 64436 não nulos no df de green_taxi. o que representa 7,34% de valores nulos nessa coluna. Sabemos que dados de corridas de taxi são passíveis de sazonalidade, e para não perdê-la na análise, vale a pena imputar nos nulos a média do período

In [0]:
%sql
--descobrindo a média de passenger_count dos green_taxis sem valor nulo, APENAS NO PERÍODO SOLICITADO
select 
round(avg(passenger_count),2) as media_passageiros_green
from curated_nyc_taxi.green_taxi_curated
where lpep_pickup_datetime >= date '2023-05-01'
and lpep_pickup_datetime <  date '2023-06-01'
and passenger_count is not null

media_passageiros_green 1.27

In [0]:
%sql
select *,
coalesce(passenger_count, 1.27) as passenger_count_imputed 
from curated_nyc_taxi.green_taxi_curated
where lpep_pickup_datetime >= timestamp '2023-05-01'
and lpep_pickup_datetime < timestamp '2023-06-01'

VendorID passenger_count total_amount lpep_pickup_datetime lpep_dropoff_datetime taxi_color passenger_count_imputed 2 1.0 31.4 2023-05-01T00:52:10.000Z 2023-05-01T01:05:26.000Z green_taxi 1.0 2 1.0 40.55 2023-05-01T00:29:49.000Z 2023-05-01T00:50:11.000Z green_taxi 1.0 2 1.0 14.16 2023-05-01T00:25:19.000Z 2023-05-01T00:32:12.000Z green_taxi 1.0 2 1.0 32.57 2023-05-01T00:07:06.000Z 2023-05-01T00:27:33.000Z green_taxi 1.0 2 1.0 9.0 2023-05-01T00:43:31.000Z 2023-05-01T00:46:59.000Z green_taxi 1.0 2 1.0 12.5 2023-05-01T00:51:54.000Z 2023-05-01T01:00:24.000Z green_taxi 1.0 2 1.0 51.25 2023-05-01T00:27:46.000Z 2023-05-01T00:49:17.000Z green_taxi 1.0 1 1.0 20.4 2023-05-01T00:27:14.000Z 2023-05-01T00:41:23.000Z green_taxi 1.0 2 1.0 20.88 2023-05-01T00:24:14.000Z 2023-05-01T00:35:16.000Z green_taxi 1.0 2 1.0 21.72 2023-05-01T00:46:55.000Z 2023-05-01T00:59:19.000Z green_taxi 1.0 2 1.0 22.9 2023-05-01T00:47:56.000Z 2023-05-01T01:03:36.000Z green_taxi 1.0 2 2.0 12.5 2023-05-01T00:01:24.000Z 2023-05-01T00:09:45.000Z green_taxi 2.0 2 2.0 44.7 2023-05-01T00:11:52.000Z 2023-05-01T01:06:57.000Z green_taxi 2.0 2 2.0 27.9 2023-05-01T00:43:51.000Z 2023-05-01T01:10:50.000Z green_taxi 2.0 2 1.0 13.32 2023-05-01T00:55:01.000Z 2023-05-01T01:02:57.000Z green_taxi 1.0 2 1.0 19.2 2023-05-01T00:55:36.000Z 2023-05-01T01:08:30.000Z green_taxi 1.0 2 1.0 15.3 2023-05-01T00:22:54.000Z 2023-05-01T00:32:09.000Z green_taxi 1.0 2 1.0 31.2 2023-05-01T00:22:55.000Z 2023-05-01T00:22:59.000Z green_taxi 1.0 2 1.0 14.6 2023-05-01T00:22:40.000Z 2023-05-01T00:30:56.000Z green_taxi 1.0 2 1.0 30.0 2023-05-01T00:53:11.000Z 2023-05-01T01:11:20.000Z green_taxi 1.0 2 1.0 7.6 2023-05-01T00:35:58.000Z 2023-05-01T00:39:08.000Z green_taxi 1.0 2 1.0 35.6 2023-05-01T01:56:45.000Z 2023-05-01T02:22:52.000Z green_taxi 1.0 2 1.0 27.6 2023-05-01T01:36:37.000Z 2023-05-01T01:53:27.000Z green_taxi 1.0 2 1.0 36.3 2023-05-01T01:56:20.000Z 2023-05-01T02:19:07.000Z green_taxi 1.0 2 1.0 16.65 2023-05-01T01:28:39.000Z 2023-05-01T01:37:06.000Z green_taxi 1.0 2 2.0 16.7 2023-05-01T01:28:41.000Z 2023-05-01T01:39:16.000Z green_taxi 2.0 2 1.0 16.68 2023-05-01T01:20:40.000Z 2023-05-01T01:29:43.000Z green_taxi 1.0 2 1.0 70.75 2023-05-01T01:44:05.000Z 2023-05-01T02:18:14.000Z green_taxi 1.0 2 1.0 9.7 2023-05-01T01:13:01.000Z 2023-05-01T01:18:39.000Z green_taxi 1.0 2 1.0 22.9 2023-05-01T01:16:35.000Z 2023-05-01T01:24:57.000Z green_taxi 1.0 2 1.0 16.7 2023-05-01T01:02:56.000Z 2023-05-01T01:16:44.000Z green_taxi 1.0 2 1.0 9.0 2023-05-01T01:25:23.000Z 2023-05-01T01:31:00.000Z green_taxi 1.0 2 1.0 15.0 2023-05-01T01:43:13.000Z 2023-05-01T01:55:58.000Z green_taxi 1.0 2 1.0 25.8 2023-05-01T02:12:11.000Z 2023-05-01T02:28:29.000Z green_taxi 1.0 2 2.0 11.8 2023-05-01T02:25:20.000Z 2023-05-01T02:31:36.000Z green_taxi 2.0 2 1.0 28.6 2023-05-01T03:00:27.000Z 2023-05-01T03:12:42.000Z green_taxi 1.0 2 1.0 39.8 2023-05-01T02:37:49.000Z 2023-05-01T03:01:27.000Z green_taxi 1.0 2 2.0 16.0 2023-05-01T02:57:35.000Z 2023-05-01T03:08:39.000Z green_taxi 2.0 2 1.0 11.8 2023-05-01T02:37:22.000Z 2023-05-01T02:44:11.000Z green_taxi 1.0 2 1.0 13.0 2023-05-01T02:29:09.000Z 2023-05-01T02:44:09.000Z green_taxi 1.0 2 1.0 11.8 2023-05-01T03:45:51.000Z 2023-05-01T03:52:37.000Z green_taxi 1.0 2 1.0 10.4 2023-05-01T03:25:56.000Z 2023-05-01T03:32:23.000Z green_taxi 1.0 2 1.0 12.42 2023-05-01T02:27:49.000Z 2023-05-01T02:30:16.000Z green_taxi 1.0 2 1.0 9.12 2023-05-01T03:49:04.000Z 2023-05-01T03:52:08.000Z green_taxi 1.0 1 1.0 9.7 2023-05-01T03:31:37.000Z 2023-05-01T03:37:05.000Z green_taxi 1.0 2 1.0 26.5 2023-05-01T03:39:22.000Z 2023-05-01T03:59:59.000Z green_taxi 1.0 1 1.0 47.55 2023-05-01T03:57:21.000Z 2023-05-01T04:18:14.000Z green_taxi 1.0 2 1.0 15.9 2023-05-01T03:54:34.000Z 2023-05-01T04:03:32.000Z green_taxi 1.0 2 1.0 6.9 2023-05-01T03:19:58.000Z 2023-05-01T03:21:59.000Z green_taxi 1.0 2 1.0 13.0 2023-05-01T03:03:49.000Z 2023-05-01T03:13:02.000Z green_taxi 1.0 2 3.0 76.0 2023-05-01T03:40:28.000Z 2023-05-01T04:12:27.000Z green_taxi 3.0 2 

criando tabela temporária green taxi com o coalesce da média nos passenger_count null

In [0]:
df_g_med_pas_count = spark.sql(
  "select *, "
  "coalesce(passenger_count, 1.27) as passenger_count_imputed "
  "from curated_nyc_taxi.green_taxi_curated "
  "where lpep_pickup_datetime >= timestamp '2023-05-01' "
  "and lpep_pickup_datetime < timestamp '2023-06-01'"
)
df_g_med_pas_count.createOrReplaceTempView("df_g_med_pas_count")

In [0]:
df_y_med_pas_count

**Analise individual da quantidade de passageiros por hora no yellow taxi no mes de Maio**

In [0]:
%sql
-- passenger count yellow taxi 
select
hour(tpep_pickup_datetime) AS hora,
SUM(COALESCE(passenger_count)) as qtd_passageiros
from df_y_med_pas_count
where  tpep_pickup_datetime >= timestamp '2023-05-01'
and tpep_pickup_datetime <  timestamp '2023-06-01'
group by 1
order by 1

hora qtd_passageiros 0 128112.0 1 83857.0 2 54693.0 3 35650.0 4 22646.0 5 23719.0 6 57865.0 7 118318.0 8 163493.0 9 186022.0 10 208480.0 11 229629.0 12 250255.0 13 257838.0 14 281460.0 15 290038.0 16 289587.0 17 314258.0 18 332393.0 19 300485.0 20 268770.0 21 278204.0 22 258812.0 23 201439.0

**## Analise individual da quantidade de passageiros por hora no green taxi**

In [0]:
%sql
-- passenger count green taxi
select
hour(lpep_pickup_datetime) AS hora,
round(sum(coalesce(passenger_count_imputed, 0)),0) as qtd_passageiros
from df_g_med_pas_count
where  lpep_pickup_datetime >= date '2023-05-01'
and lpep_pickup_datetime <  date '2023-06-01'
group by 1
order by 1

hora qtd_passageiros 0 1612.0 1 1061.0 2 830.0 3 672.0 4 539.0 5 573.0 6 1517.0 7 3354.0 8 4019.0 9 4534.0 10 4486.0 11 4982.0 12 5005.0 13 4595.0 14 5551.0 15 5962.0 16 6371.0 17 6521.0 18 6738.0 19 5376.0 20 4340.0 21 3764.0 22 3085.0 23 2285.0

**## RESULTADO Q2: MÉDIA DE PASSAGEIROS POR HORA QUE PEGARAM TAXI NO MES DE MAIO CONSIDERANDO AMBAS AS FROTAS.**

In [0]:
%sql
--Analise da media de passageiros por hora que pegaram taxi no mes de maio de ambas as frotas
with yellow as (
select
hour(tpep_pickup_datetime) AS hora,
round(sum(passenger_count_imputed),0) as qtd_passageiros
from df_y_med_pas_count
where  tpep_pickup_datetime >= date '2023-05-01'
and tpep_pickup_datetime <  date '2023-06-01'
group by 1
order by 1
),
green as (
select
hour(lpep_pickup_datetime) AS hora,
round(sum(passenger_count_imputed),0) as qtd_passageiros
from df_g_med_pas_count
where  lpep_pickup_datetime >= date '2023-05-01'
and lpep_pickup_datetime <  date '2023-06-01'
group by 1
order by 1
),
total as (
select
*
from yellow
union all
select
*
from green
)
select 
hora,
round(avg(qtd_passageiros),0) as media_passageiros
from total
group by 1
order by 1

hora media_passageiros 0 67089.0 1 44027.0 2 28863.0 3 19011.0 4 12760.0 5 13200.0 6 31476.0 7 64310.0 8 88086.0 9 98819.0 10 109464.0 11 120270.0 12 130785.0 13 134392.0 14 147025.0 15 151661.0 16 151627.0 17 164460.0 18 173739.0 19 156332.0 20 139450.0 21 144294.0 22 134753.0 23 105232.0